In [0]:
brand_df=spark.sql("select * from dev.dimbrand ")
date_df=spark.sql("select * from dev.dimdate ")
fuel_df=spark.sql("select * from dev.dimfuel ")
loc_df=spark.sql("select * from dev.dimlocation ")
model_df=spark.sql("select * from dev.dimmodel ")
transmission_df=spark.sql("select * from dev.dimtransmission ")
fact4W_df= spark.sql("select * from dev.factsalesoffourwheeler ")

In [0]:
fact4W_df.printSchema()

root
 |-- pkSalesId: long (nullable = true)
 |-- fkBrandId: long (nullable = true)
 |-- fkModelId: long (nullable = true)
 |-- fkFuelId: long (nullable = true)
 |-- fkTransmissionId: long (nullable = true)
 |-- fkDateId: long (nullable = true)
 |-- fkLocationId: long (nullable = true)
 |-- Mileage: string (nullable = true)
 |-- TopSpeed: string (nullable = true)
 |-- Pricerange: string (nullable = true)
 |-- NoOfCylinders: integer (nullable = true)
 |-- RowId: string (nullable = true)



In [0]:
from pyspark.sql.types import *
from pyspark.sql.functions import *
from pyspark.sql import SparkSession


source_df=spark.read.format('parquet').option('header',True).load("dbfs:/Silver/4_wheelers/202403/29/*.parquet")


join_df=source_df.join(model_df.select('ModelName','pkModelId'),source_df.model==model_df.ModelName,'left')\
    .join(brand_df,source_df.brand==brand_df.BrandName,'left')\
    .join(date_df.select('DateId','Year'),source_df.yearofsale==date_df.Year,'left')\
    .join(loc_df.select('pkLocationId','Country','City'),source_df.city==loc_df.City,'left')\
    .join(transmission_df.select('pkTransmissionId','Transmission'),source_df.transmission==transmission_df.Transmission,'left')\
    .join(fuel_df.select('pkFuelId','FuelType'),source_df.fueltype==fuel_df.FuelType,'left')
print('join df')
join_df.show()
  

final1_df = join_df.select(
    col('pkBrandID').alias('fkBrandID'),
    col('pkModelId').alias('fkModelID'),
    col('pkFuelId').alias('fkFuelID'),
    col('pkTransmissionID').alias('fkTransmissionID'),
    col('DateID').alias('fkDateID'),
    col('pkLocationId').alias('fkLocationID'),
    col('Mileage').alias('Mileage'),
    col('top_speedinkm/h').alias('TopSpeed'),
    col('pricerange').alias('Pricerange'),
    col('noofcylinders').alias('NoOfCylinders')
).distinct()


finalfact= final1_df.withColumn(
    "RowId",
    md5(
        concat_ws(",", 
            col('fkBrandID').cast("string"),
            col('fkModelID').cast("string"),
            col('fkFuelID').cast("string"),
            col('fkTransmissionID').cast("string"),
            col('fkDateID').cast("string"),
            col('fkLocationID').cast("string"),
            col('Mileage').cast("string"),
            col('TopSpeed').cast("string"),
            col('Pricerange').cast("string")
        )
    )
)  

newrec_df = finalfact.join(fact4W_df, 'RowId', 'left_anti').withColumn('fkModelID', col('fkModelID').cast(LongType())).withColumn('fkBrandID', col('fkBrandID').cast(LongType()))
# newrec_df.show()
# newrec_df.printSchema()
newrec_df.write.mode('append').saveAsTable('dev.factsalesoffourwheeler')
print("done")

join df
+-------+-----+-------+--------+-------+---------------+------------+------------------+---------------+---------------+---------------+-------------+----------+-----------+-------+---------+---------+---------+---------+---------+----------+------+----+------------+-------+---------+----------------+------------+--------+--------+
|  brand|model|segment|fueltype|mileage| enginecapacity|transmission|        pricerange|fuelcapacity(l)|seatingcapacity|top_speedinkm/h|noofcylinders|yearofsale|monthofsale|country|     city|ModelName|pkModelId|pkBrandId|BrandName|WheelerKey|DateId|Year|pkLocationId|Country|     City|pkTransmissionId|Transmission|pkFuelId|FuelType|
+-------+-----+-------+--------+-------+---------------+------------+------------------+---------------+---------------+---------------+-------------+----------+-----------+-------+---------+---------+---------+---------+---------+----------+------+----+------------+-------+---------+----------------+------------+--------+

In [0]:
%sql
select * from dev.factsalesoffourwheeler

pkSalesId fkBrandId fkModelId fkFuelId fkTransmissionId fkDateId fkLocationId Mileage TopSpeed Pricerange NoOfCylinders RowId 1 18 323 1 2 17 11 9 kmpl 275 85.46 Lakh - 1.64 Crore 8 694e8c92bb44dcbfe643f215344207ff 2 18 323 1 1 18 16 9 kmpl 275 85.46 Lakh - 1.64 Crore 8 d357ebb8079f175c9398420592efb272 3 12 329 1 1 19 11 14 kmpl 250 55.86 - 60.51 Lakh 6 55d2291caf02474bd56f51123c961194 4 12 548 1 1 18 9 11 kmpl 250 79.06 Lakh 8 d6be3908403313aac9b930ba600aa768 5 10 427 3 1 18 15 17 kmpl 225 77.25 - 94.22 Lakh 8 5d317151fbfc09b62383383c5ba5ff87 6 10 422 3 1 19 15 7 - 12 kmpl 210 1.62 - 2.42 Crore 6 28015d1242f8f77c65c61d6698c1dbe4 7 10 361 1 1 19 22 14 - 16 kmpl 240 49.41 - 65.55 Lakh 6 568b393f93eea9887ff160f6e46b499a 8 10 333 1 1 19 22 9 kmpl 261 81.22 Lakh 8 480176f88d262a0b739367d2f9e11d30 9 10 428 3 1 17 3 8-9 kmpl 222 1.05 Crore 6 101f84b9aedb87b24a42c7d14e9a06ab 10 10 427 3 1 17 12 17 kmpl 225 77.25 - 94.22 Lakh 8 f3a5dcc6d2dde6125acc9cfd1da22fb0 11 10 327 3 1 18 12 13 - 21 kmpl 250 39.9 - 56.24 Lakh 6 86e7e9d1e1216e40e2abdc7780961422 12 10 412 2 1 19 12 6 kmpl 180 1.04 Crore 6 dfee09fcfa66de0286518f44858641e6 13 10 334 1 1 17 6 11 kmpl 225 1.27 Crore 8 3c42c69bb9e1ea24f3dad6ccf6b5ffa4 14 10 412 2 1 19 6 6 kmpl 180 1.04 Crore 6 216b359f3906e42d2901037d1d9e53e5 15 10 333 1 1 17 10 9 kmpl 261 81.22 Lakh 8 d2db3a6185a70f5a74917942bad9f73b 16 11 588 1 1 19 22 20 kmpl 222 37.2 - 42.9 Lakh 6 d6886cc31a23a4bc5db0e9c259c935f8 17 11 589 1 1 17 11 13 - 16 kmpl 213 56.5 - 62.5 Lakh 6 d61467b8145027973b2c16edbbf56f8d 18 11 592 1 1 19 11 13 kmpl 300 75.5 - 87.4 Lakh 6 c95a9f372c300c8194b81e0c4f55e3cc 19 11 315 1 1 17 5 14 - 19 kmpl 233 37.9 - 42.3 Lakh 8 b30d59ffbcf9576a29991ff381879b81 20 11 319 3 1 19 9 15 - 20 kmpl 250 56 - 69.1 Lakh 6 9ae9fbeeb81680bdd6b4b3aec7c3bbb2 21 11 315 1 1 17 25 14 - 19 kmpl 233 37.9 - 42.3 Lakh 8 69d1089a404a72ab7326271f2a90bb2b 22 11 318 1 1 17 26 15 - 20 kmpl 250 56 - 69.1 Lakh 6 3dbafa44bf31a4c308d142cdba1d5ad1 23 11 315 1 1 19 26 14 - 19 kmpl 233 37.9 - 42.3 Lakh 8 8b14ce28da4b37d2ff26553a56184aa4 24 11 591 1 1 17 17 13 - 16 kmpl 235 62.4 - 68.9 Lakh 6 7c8f61f6eec7af80efe74103b29e7a18 25 11 322 1 1 19 16 8 - 40 kmpl 310 1.38 - 2.46 Crore 6 47e5c6ae8ac7e54aef025bf135695b59 26 11 322 3 1 18 20 8 - 40 kmpl 310 1.38 - 2.46 Crore 6 00f6608e370aea18a31e3ffc7eaffdd6 27 9 415 1 1 19 4 8 - 12 kmpl 250 95.12 Lakh - 2.54 Crore 8 70ead3c3973d46af72fd17b83c487d22 28 9 459 2 1 19 6 470 km 200 1.06 - 1.12 Crore 6 3f3f2767279f5981e192781348ad3364 29 19 578 3 1 17 22 12.5 kmpl 180 65.41 Lakh 4 8bbadc5f0d1700b7e723379656c93454 30 19 596 1 1 18 4 15 kmpl 180 39.9 Lakh 6 d7222abbdff3aa21502737c546c16c14 31 13 495 1 1 19 22 18 kmpl 180 58.2 - 63.63 Lakh 6 209c0f01733c0c8e10d2bfc8773882b2 32 13 413 1 1 18 11 9 kmpl 210 56.55 - 61.75 Lakh 6 c64f04139a14ffce82129cd8e44a415f 33 13 477 1 1 17 5 12 kmpl 205 1.91 - 2.22 Crore 6 35a94728f507b33823175e8476e380d0 34 13 413 1 1 17 19 9 kmpl 210 56.55 - 61.75 Lakh 6 8db3d32143d3af869881b9a1d2de7491 35 14 325 1 1 18 4 14 kmpl 340 5.2 Crore 8 0df0b9313c2b7845d9445592793e78bd 36 15 393 1 1 19 19 6-7 kmpl 250 6.95 Crore 6 e68768251f84494f729b2d6adb993948 37 16 433 3 1 17 3 16.9 kmpl 286 1.15 - 1.92 Crore 6 1955445564014a88be99a16d9c4e46ce 38 18 326 1 1 19 10 9 - 12 kmpl 330 1.64 - 3.08 Crore 8 574608009cca3a934ce38d9ab1911001 39 18 385 1 1 17 26 10.75 kmpl 286 1.32 - 1.98 Crore 8 ce7a836a421527bc474ccfff986b1e08 40 18 486 1 1 18 25 14 kmpl 254 69.98 - 85.01 Lakh 6 93a5f5543146dbe84aaa2b2fbe7b981f 41 12 329 1 1 18 21 14 kmpl 250 55.86 - 60.51 Lakh 6 a2165e0d85099e411aac92d755722e74 42 12 526 1 1 17 6 16 kmpl 250 98.98 Lakh - 1.35 Crore 6 6ffc886dd7e0caaa4792b63dc9f4c73b 43 12 526 1 1 18 10 16 kmpl 250 98.98 Lakh - 1.35 Crore 6 04832e3efd7b36394be1d0e71a637e3d 44 12 535 1 1 19 26 8 kmpl 305 2.07 Crore 6 28f01bf61d739fc731af168daf1e6f47 45 12 526 1 1 19 17 16 kmpl 250 98.98 Lakh - 1.35 Crore 6 ddfb394f9543a87bce6d38ad6f76bc7b 46 10 378 3 1 18 4 12 kmpl 250 86.39 Lakh 8 d0ad15ea35bdff1ce510

In [0]:
%sql
truncate table dev.factsalesoffourwheeler

In [0]:
# from pyspark.sql.types import *
# from pyspark.sql.functions import *
# from pyspark.sql import SparkSession


# source_df=spark.read.format('parquet').option('header',True).load("dbfs:/Silver/4_wheelers/202403/23/*.parquet")

# dim_brand_df=brand_df.filter(col('WheelerKey') =='F').select('BrandName','pkBrandID')
# dim_locatiion_df=loc_df.filter(col('WheelerKey') == 'F').select('City','Country','pkLocationId')
# dim_fuel_df=fuel_df.filter(col('WheelerKey') == 'F').select('FuelType','pkFuelId')
# dim_Transmission_df=transmission_df.filter(col('WheelerKey') == 'F').select('pkTransmissionID','Transmission')

# join_df = source_df.join(model_df.select('ModelName', 'enddate', 'pkModelId'),source_df['model'] == model_df['ModelName'],'left'
# ).join(dim_brand_df,source_df['brand'] == brand_df['BrandName'],'left'
# ).join(date_df.select('Year', 'DateID'),source_df['yearofsale'] == date_df['Year'],'left'
# ).join(dim_locatiion_df,(source_df['city'] == loc_df['City']) & (source_df['City'] == loc_df['City']),'left'
# ).join(dim_Transmission_df,source_df['TRANSMISSION'] == transmission_df['Transmission'],'left'
# ).join(dim_fuel_df,source_df['fueltype'] == fuel_df['FuelType'],'left')

# final1_df = join_df.select(
#     col('pkBrandID').alias('fkBrandID'),
#     col('pkModelId').alias('fkModelID'),
#     col('pkFuelId').alias('fkFuelID'),
#     col('pkTransmissionID').alias('fkTransmissionID'),
#     col('DateID').alias('fkDateID'),
#     col('pkLocationId').alias('fkLocationID'),
#     col('Mileage').alias('Mileage'),
#     col('top_speedinkm/h').alias('TopSpeed'),
#     col('pricerange').alias('Pricerange'),
#     col('noofcylinders').alias('NoOfCylinders')
# ).distinct()


# finalfact= final1_df.withColumn(
#     "RowId",
#     md5(
#         concat_ws(",", 
#             col('fkBrandID').cast("string"),
#             col('fkModelID').cast("string"),
#             col('fkFuelID').cast("string"),
#             col('fkTransmissionID').cast("string"),
#             col('fkDateID').cast("string"),
#             col('fkLocationID').cast("string"),
#             col('Mileage').cast("string"),
#             col('TopSpeed').cast("string"),
#             col('Pricerange').cast("string"),
#             col('noofcylinders').alias('NoOfCylinders')
#         )
#     )
# )  

# newrec_df = finalfact.join(fact4W_df, 'RowId', 'left_anti').withColumn('fkModelID', col('fkModelID').cast(LongType())).withColumn('fkBrandID', col('fkBrandID').cast(LongType()))
# newrec_df.show()
# newrec_df.printSchema()
# newrec_df.write.mode('append').saveAsTable('dev.FactSalesOfFourWheeler')
# print("done")

+--------------------+---------+---------+--------+----------------+--------+------------+-----------+--------+--------------------+-------------+
|               RowId|fkBrandID|fkModelID|fkFuelID|fkTransmissionID|fkDateID|fkLocationID|    Mileage|TopSpeed|          Pricerange|NoOfCylinders|
+--------------------+---------+---------+--------+----------------+--------+------------+-----------+--------+--------------------+-------------+
|a3e5490021dca5ba5...|     null|       72|    null|            null|      17|          14|9 - 40 kmpl|     286|    1.2 - 1.93 Crore|            6|
|395c8de7835957404...|     null|       11|    null|            null|      17|          14|     9 kmpl|     275|85.46 Lakh - 1.64...|            8|
|7da28991f5975aeb2...|     null|       11|    null|            null|      19|          14|     9 kmpl|     275|85.46 Lakh - 1.64...|            8|
|487c95af9a6992594...|     null|       11|    null|            null|      18|          11|     9 kmpl|     275|85.46 L